In [10]:
import uproot
import numpy as np
import awkward as ak

import ROOT

import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

In [6]:
class Encoder(nn.Module):
    def __init__(self, embed_dim, num_heads):
        super(Encoder, self).__init__()
        self.pre_norm_Q = nn.LayerNorm(embed_dim)
        self.pre_norm_K = nn.LayerNorm(embed_dim)
        self.pre_norm_V = nn.LayerNorm(embed_dim)
        self.attention = nn.MultiheadAttention(embed_dim,num_heads=num_heads,batch_first=True, dropout=0.25)
        self.post_norm = nn.LayerNorm(embed_dim)
        self.out = nn.Linear(embed_dim,embed_dim)
    def forward(self, Query, Key, Value):
        Query = self.pre_norm_Q(Query)
        Key = self.pre_norm_K(Key)
        Value = self.pre_norm_V(Value)
        context, weights = self.attention(Query, Key, Value)
        context = self.post_norm(context)
        latent = Query + context
        tmp = F.gelu(self.out(latent))
        latent = latent + tmp
        return latent, weights

class Model(nn.Module):  
    def __init__(self):
        super(Model, self).__init__()   
        
        self.embed_dim = 256
        self.num_heads = 4
        self.num_jet_feats = 4
        self.num_trk_feats = 6
        
        self.jet_initializer = nn.Linear(self.num_jet_feats, self.embed_dim)
        self.jet_trk_initializer = nn.Linear(self.num_trk_feats, self.embed_dim)
        self.trk_initializer = nn.Linear(self.num_trk_feats, self.embed_dim)
            
        # Track Encoder Stack
        self.trk_encoder1 = Encoder(self.embed_dim, self.num_heads)
        self.trk_encoder2 = Encoder(self.embed_dim, self.num_heads)
        self.trk_encoder3 = Encoder(self.embed_dim, self.num_heads)
        self.jet_postprocess = nn.Linear(self.embed_dim*2, self.embed_dim)
        
        # All Track Encoder Stack
        self.all_trk_encoder1 = Encoder(self.embed_dim, self.num_heads)
        self.all_trk_encoder2 = Encoder(self.embed_dim, self.num_heads)
        self.all_trk_encoder3 = Encoder(self.embed_dim, self.num_heads)
        
        # Cross Encoder Stack
        self.cross_encoder1 = Encoder(self.embed_dim, self.num_heads)
        self.cross_encoder2 = Encoder(self.embed_dim, self.num_heads)
        self.cross_encoder3 = Encoder(self.embed_dim, self.num_heads)
        
        # Jet Encoder Stack
        self.jet_encoder1 = Encoder(self.embed_dim, self.num_heads)
        self.jet_encoder2 = Encoder(self.embed_dim, self.num_heads)
        self.jet_encoder3 = Encoder(self.embed_dim, self.num_heads)

        # Regression Task
        self.regression = nn.Linear(self.embed_dim, 1)
        
    def forward(self, jets, jet_trks, trks):
        # Feature preprocessing layers
        jet_init = F.relu(self.jet_initializer(jets))
        jet_trk_init = F.relu(self.jet_trk_initializer(jet_trks))
        trk_init = F.relu(self.trk_initializer(trks))
        
        # Calculate aggregated tracks using attention
        jet_trk_embedding, trk_weights = self.trk_encoder1(jet_trk_init, jet_trk_init, jet_trk_init)
        jet_trk_embedding, trk_weights = self.trk_encoder2(jet_trk_embedding, jet_trk_embedding, jet_trk_embedding)
        jet_trk_embedding, trk_weights = self.trk_encoder3(jet_trk_embedding, jet_trk_embedding, jet_trk_embedding)
        
        # Generate meaningful jet_embedding using info from trk_aggregated  
        jet_trk_aggregated = jet_trk_embedding.sum(dim=1)
        jet_embedding = torch.cat((jet_init, jet_trk_aggregated),1)
        jet_embedding = F.relu(self.jet_postprocess(jet_embedding))
        
        # All Track Attention
        all_trk_embedding, all_trk_weights = self.all_trk_encoder1(trk_init, trk_init, trk_init)
        all_trk_embedding, all_trk_weights = self.all_trk_encoder2(all_trk_embedding, all_trk_embedding, all_trk_embedding)
        all_trk_embedding, all_trk_weights = self.all_trk_encoder3(all_trk_embedding, all_trk_embedding, all_trk_embedding)

        # Cross Attention
        jet_embedding, cross_weights = self.cross_encoder1(jet_embedding, all_trk_embedding, all_trk_embedding)
        jet_embedding, cross_weights = self.cross_encoder2(jet_embedding, all_trk_embedding, all_trk_embedding)
        jet_embedding, cross_weights = self.cross_encoder3(jet_embedding, all_trk_embedding, all_trk_embedding)
        
        # Update embeddings of jets in the contex of entire event
        jet_embedding, jet_weights = self.jet_encoder1(jet_embedding, jet_embedding, jet_embedding)
        jet_embedding, jet_weights = self.jet_encoder2(jet_embedding, jet_embedding, jet_embedding)
        jet_embedding, jet_weights = self.jet_encoder3(jet_embedding, jet_embedding, jet_embedding)
        
        # Get output
        output = F.sigmoid(self.regression(jet_embedding))
        
        return output, jet_weights, trk_weights, cross_weights

In [7]:
PUFNN = torch.load("PUFNN.torch")

/tmp/ipykernel_2296502/3925552895.py:1: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  PUFNN = torch.load("PUFNN.torch")


In [22]:
with uproot.open("../pythia/output/dataset_4b_FILTER60_mu60_NumEvents10k_MinJetpT25.root:fastjet") as f:
    jet_pt = f["jet_pt"].array()
    jet_eta = f["jet_eta"].array()
    jet_phi = f["jet_phi"].array()
    jet_corrJVF = f["jet_corrJVF"].array()
    jet_RpT = f["jet_RpT"].array()
    jet_m = f["jet_m"].array()
    trk_pt = f["trk_jet_pT"].array()
    trk_eta = f["trk_jet_eta"].array()
    trk_phi = f["trk_jet_phi"].array()
    trk_q = f["trk_jet_q"].array()
    trk_d0 = f["trk_jet_d0"].array()
    trk_z0 = f["trk_jet_z0"].array()
    trk_label = f["trk_jet_label"].array()
    jet_trk_IDX = f["jet_track_index"].array()
    jet_pufr_truth = f["jet_pufr_truth"].array()

In [21]:
f = ROOT.TFile("../pythia/output/dataset_4b_FILTER60_mu60_NumEvents10k_MinJetpT25.root")
myTree = f.Get("fastjet")

for i in range(myTree.GetEntriesFast()):
    myTree.GetEntry(i)
    val = myTree.jet_pt
    print(np.array(val))

[146.49944  106.520096  92.097595  69.35179   61.795723  60.820583
  59.999294  59.916412  59.09856   53.437565  52.794086  52.656403
  51.93043   51.86894   51.84283   51.79195   50.14343   49.051212
  48.958355  48.32616   47.793808  47.666832  47.56847   47.323803
  46.901382  46.45509   46.000618  45.468533  45.38324   45.377563
  45.30263   44.844517  44.261047  43.872055  42.386078  41.449894
  41.17009   40.819946  40.799385  40.699005  40.640392  40.25178
  39.531376  39.499264  38.992325  38.876057  38.124905  37.976624
  37.85577   37.67451   37.377644  37.267113  36.44014   35.630203
  34.90796   34.51604   34.494156  34.135536  34.118053  33.942398
  33.584522  33.425262  33.26458   33.262703  32.769093  32.47945
  32.466183  32.022995  31.81012   31.709766  31.63593   31.504274
  31.390394  30.904083  30.799582  30.630976  30.482944  30.44994
  30.389423  30.335087  30.110579  29.225124  29.20937   29.12949
  29.022552  28.010149  27.870377  27.826235  27.70372   27.643942

[83.64097  79.680214 69.99222  64.749306 58.039547 42.901104 42.185417
 40.925995 39.48676  39.16084  36.85063  36.103546 35.45078  35.05125
 30.963213 30.793015 30.440489 30.263554 30.23992  29.965014 29.69212
 29.397564 29.372831 28.987047 28.838135 28.556475 28.289904 28.224419
 28.194984 27.895346 27.808105 27.699558 26.294874 26.101866 25.93083
 25.309662]
[126.23254  116.881966 108.2336    81.822815  69.93935   66.57013
  60.708107  59.20322   57.39502   53.37823   49.41739   46.430744
  45.185383  44.227997  43.065754  42.712257  42.67393   41.736584
  41.639637  41.319126  41.089607  40.903736  39.881027  39.691097
  38.810253  38.695168  37.710155  37.421078  37.301594  37.022713
  37.02134   36.866356  36.74089   36.598072  35.889694  35.476215
  35.13732   34.95933   34.380787  34.066902  34.062172  33.992493
  33.76074   33.725643  32.949577  32.844643  32.588184  32.327557
  32.19692   31.916319  31.885485  31.88283   31.767725  31.71731
  31.401197  31.377037  31.098423  

[383.82584  293.7356   202.576     63.061535  62.17047   57.129627
  53.947266  52.225357  50.978268  46.178093  45.796654  43.86449
  42.22739   42.212006  42.019215  41.440617  40.721523  39.212204
  38.84437   38.58753   38.103764  37.7185    37.664215  37.037117
  35.600506  35.14981   35.025978  35.020416  34.806442  32.612366
  32.39499   32.090706  31.983269  31.664467  31.468391  31.117645
  30.862593  30.730886  30.509266  30.436935  29.693954  29.58147
  29.464214  29.249756  28.843452  28.734798  28.581127  28.552164
  28.410856  28.348196  27.750225  27.663284  27.450848  27.26177
  27.07903   26.957706  26.942627  26.90432   26.383572  25.96708
  25.921396  25.89019   25.865227  25.602722  25.499292  25.460976
  25.269281  25.220196  25.051485]
[141.91437  140.62701  125.86148  108.1742    88.2777    57.293056
  54.72142   52.53169   50.965855  47.52643   46.292854  43.95583
  43.370895  43.218597  42.33802   41.968243  41.807255  41.44413
  41.139896  40.06866   39.660206

[160.26021  103.19125   99.55171   97.07986   74.675354  74.66984
  72.82785   69.42461   68.14867   57.07378   53.87528   53.3903
  47.414516  46.44216   44.79811   44.794968  44.099693  43.80886
  41.646122  40.930557  40.547855  38.469437  38.292145  37.346996
  36.922127  36.819763  34.90035   34.745483  34.269154  34.262455
  33.677963  33.305607  33.294674  32.77651   32.548317  32.54811
  32.543762  32.112114  31.978079  31.883724  31.761387  30.440483
  29.90172   29.818867  29.147299  29.051172  28.688961  28.563143
  28.480206  28.401329  28.28466   28.02152   27.995895  27.991125
  27.661692  27.57539   27.398739  27.247252  26.918312  26.914936
  26.884848  26.374378  26.172363  25.75144   25.420515  25.358568]
[197.46617  140.10562  127.61589   99.11698   97.95823   81.92432
  65.387115  55.44463   50.402588  44.992867  42.457153  41.910316
  41.324608  40.376442  40.115856  38.65724   37.563812  37.371864
  37.34397   36.64404   35.703426  34.439564  34.396763  34.2505
  

[177.80214  153.93373  125.77693   96.67536   82.34455   80.39739
  78.01492   69.517456  58.657368  57.61326   51.712135  51.632744
  51.211857  49.15058   48.7336    47.83248   47.649605  47.008793
  45.806362  45.36253   44.895775  44.252026  42.86246   41.929016
  41.860664  41.59691   41.00172   40.788177  40.46445   39.94743
  39.640984  39.372932  38.73257   37.761227  37.661983  37.603134
  37.340897  37.279522  37.179142  36.970135  36.751213  36.458103
  36.233017  35.991848  35.97931   35.86605   35.689575  35.44557
  35.25126   34.94907   34.805725  34.752895  33.97049   33.828804
  33.246487  32.751015  32.47477   32.312954  31.992254  31.677156
  31.644268  31.604418  31.40966   31.124512  31.079872  30.921282
  30.61756   30.47316   30.149218  29.95288   29.453142  29.42939
  29.427166  29.133232  28.591452  28.065632  28.064272  27.886658
  27.68662   27.655678  27.646048  27.406982  27.269186  27.193409
  27.157167  26.765005  26.6859    26.656906  26.326859  26.06068


...

[94.50138  83.0699   81.13251  80.0728   76.70109  67.04672  62.958267
 61.40545  59.95519  54.86233  50.484608 48.728092 48.33614  47.360054
 46.599194 44.72257  41.42673  40.599422 39.732685 39.56895  39.27055
 38.642593 38.543194 38.493496 38.132576 38.04958  38.030518 37.942448
 37.294777 37.020187 36.93574  36.618073 36.46877  35.69859  35.1221
 35.020504 34.869038 34.713737 34.676083 33.91257  33.688343 33.56758
 33.31981  33.09635  33.005527 32.964798 32.861916 32.848915 32.426514
 32.239826 31.753517 31.459028 30.926888 30.55437  30.28992  30.204762
 29.82566  29.783693 29.760145 29.643887 29.564386 29.526783 29.452156
 29.369772 29.333868 29.239857 27.861511 27.610981 27.526682 27.187555
 26.839495 26.706322 26.087011 25.906507 25.677309 25.579264 25.577276
 25.519932 25.16651 ]
[208.83641  200.20244  156.44348  102.90492   56.924297  54.46096
  54.1868    50.88301   48.229454  45.921124  44.996094  44.22897
  43.579475  43.497036  42.849495  42.449158  42.15232   40.31466
  3

[173.43904  143.79286   61.506687  49.441467  49.25239   48.854908
  45.20217   44.32107   43.013317  42.84576   41.723858  41.04227
  40.47642   39.119415  39.098873  38.86768   38.68135   38.065205
  37.847294  37.52553   36.905445  36.850185  36.361076  36.349617
  35.79967   35.761517  35.589394  34.762577  33.236404  33.168026
  33.041683  32.96171   32.7297    32.169434  32.115383  31.767664
  31.372063  31.335482  31.271477  30.949066  30.89807   30.439943
  30.27188   30.206675  30.114285  30.095072  29.740267  29.193108
  29.04545   28.535332  28.51322   28.274992  28.214407  28.20406
  28.161129  28.139465  28.127663  27.762266  27.589924  27.059153
  26.416546  25.748632  25.747526  25.49461   25.428864  25.33135 ]
[570.6043   438.66492  147.72993  117.98278   88.86195   51.15002
  47.330643  45.59068   40.271645  39.47126   38.040253  38.02742
  35.182198  34.83216   34.322834  34.161358  34.03689   33.61784
  33.61004   31.997206  31.954771  29.76158   29.755232  29.516481

[288.72086  267.41614   73.5688    61.46454   55.374245  51.623474
  50.551327  49.85106   49.408604  48.74464   48.136406  47.779774
  47.679317  47.55813   46.178875  46.096508  46.088467  45.65673
  45.329403  44.75409   44.706066  44.663086  44.433834  44.299213
  43.414703  42.555077  42.542645  42.36638   41.67598   41.47809
  40.59549   40.42907   40.4192    40.15074   40.005657  39.909405
  39.786747  39.412914  39.17266   38.93403   38.841614  38.638638
  38.16757   37.997627  37.852707  37.83297   37.61272   37.509705
  37.315857  36.41113   36.396664  36.256462  36.183964  35.986645
  35.845913  35.812546  35.58037   35.409084  35.074375  34.969707
  34.921055  34.626446  34.534473  34.395245  34.192417  34.168602
  34.09768   33.922855  32.792072  32.54419   32.04551   31.409811
  31.107897  31.00177   30.781015  30.459286  30.313534  30.10669
  29.953987  29.804405  28.868538  28.653255  28.388706  28.277897
  27.868229  27.452982  27.443977  27.265907  27.097286  26.86431

[407.53006  261.92084  140.73108   40.973774  40.10691   35.367596
  34.493164  33.185852  32.13046   31.405367  30.066305  29.383867
  29.20554   29.127817  28.684202  28.434679  27.443098  26.704714
  26.567284  26.534626  25.886978  25.7189    25.328192  25.170551
  25.160814]
[134.0006   128.0503   105.49196   86.34      81.948235  81.346695
  61.971306  60.04081   60.02589   58.843628  56.859856  56.650414
  55.726707  51.95056   50.70124   50.279762  50.184994  49.655815
  48.705135  48.141113  48.06414   47.163456  46.577717  44.865
  44.15058   43.89592   43.664883  43.540867  43.401657  43.28955
  43.10665   43.05006   42.80082   42.52999   42.44878   41.4203
  40.929684  40.92324   40.82259   40.22222   40.11113   39.602882
  38.599632  37.820698  37.440643  36.496033  36.395203  36.320312
  35.85328   35.811302  35.376038  34.99261   34.916363  34.69854
  34.696922  34.2121    34.093224  34.061348  33.873142  33.62902
  33.470364  33.451736  33.31251   33.246056  32.782257  

[136.43387  102.06715   97.199745  86.98227   82.35258   76.627235
  70.02259   67.39478   64.84135   54.749096  52.163826  48.148342
  47.68769   46.47496   46.039406  45.991474  45.4374    44.724167
  44.140724  43.87836   43.52862   43.16535   42.61735   42.487812
  41.16448   41.043697  40.64792   40.620274  39.698246  39.63822
  39.61895   39.12555   38.94862   38.586807  38.10602   37.86534
  36.93873   36.703327  36.422245  36.209183  34.345543  34.27342
  34.197063  34.180004  33.778618  33.54529   33.49463   33.279385
  32.860073  32.397896  31.711876  31.188301  30.970366  30.3042
  29.900824  29.783045  29.527636  29.332493  29.097383  29.035616
  29.004019  28.789598  28.566412  28.428013  28.329653  26.908749
  26.586067  26.119354  26.037304  25.8557    25.50558   25.045872]
[178.39667  135.48486  114.12477   90.30043   63.50252   53.615715
  52.394875  51.805416  51.387825  50.909317  50.85138   50.060455
  47.75022   47.74305   47.341965  46.860615  44.62621   44.460243

In [ ]:
print(val)

In [ ]:
value = np.array(val)

In [2]:
import random

In [3]:
list1 = [1,2,3]
list2 = [1,0,0]
list3 = [[1,2,3],[4,5,6],[7,8,9]]

tmp = list(zip(list1,list2,list3))
random.shuffle(tmp)
l1, l2, l3 = list(zip(*tmp))

In [4]:
print(l1)
print(l2)
print(l3)

(2, 3, 1)
(0, 0, 1)
([4, 5, 6], [7, 8, 9], [1, 2, 3])
